In [1]:
import numpy as np
from numba import njit

@njit
def score_numba(x, y, blosum_matrix, gap_open=-800000, gap_extend=-80000):
    
    m = x.shape[0]
    n = y.shape[0]

    s_max = 0
    indeks = 0
    for i in range(n-m+1):
        s = 0
        for j in range(m):
            s+= blosum_matrix[y[i+j],x[j]]
        
        if s > s_max:
            s_max = s
            indeks = i

    
    return s_max,  y[indeks: indeks+m]


In [2]:
testna = "FVFGDSLSDA"
proteins_file = "zad4_AT.fasta"
blosum_file = "zad3_blosum50.txt"
acids_file = "zad3_acids.txt"
ids = []
kiseline = []
scores = []

In [3]:
f1=open(acids_file, "r")
amino_acids=f1.readline()
f1.close()

blosum_matrix=[]   
f1=open(blosum_file, "r")
for i in range(20):
    line=f1.readline()
    vc=line.split()
    blosum_matrix.append(vc[:])
for i in range(20):
    for j in range(20):
        blosum_matrix[i][j]=int(blosum_matrix[i][j])
f1.close()

In [18]:
from Bio import SeqIO
import numpy as np

rijecnik = {znak: i for i,znak in enumerate(amino_acids)} # ovo je za numbu
testna_np = np.zeros(len(testna))
for i in range(len(testna)):
    testna_np[i] = rijecnik[testna[i]]

max= 0
scores = []
nizovi = []

podaci = np.zeros((33410,5336))
duljine = np.zeros((33410,))

blosum_matrix_np = np.array(blosum_matrix)
for i,record in enumerate(SeqIO.parse(proteins_file, "fasta")):
    ids.append(record.id)
    kiseline.append(record.seq)

    record_np = np.zeros(len(record.seq)) # ovo je prebacivanje u np za numba
    for j in range(len(record.seq)):
        record_np[j] = rijecnik[record.seq[j]]


    record_np = record_np.astype(np.int32)
    testna_np = testna_np.astype(np.int32)
    blosum_matrix_np = blosum_matrix_np.astype(np.int32)

        
    podaci[i,: len(record.seq)] = record_np
    duljine[i] = len(record.seq)
    
    score, niz= score_numba(testna_np,record_np,blosum_matrix_np)
    scores.append(score)
    nizovi.append(niz)

In [5]:
scores_sorted= scores.copy()
scores_sorted.sort(reverse=True)
scores_sorted = np.array(scores_sorted)

sorted_indices = [i for i, _ in sorted(enumerate(scores), key=lambda x: x[1], reverse=True)]


In [6]:
@njit
def score_from_prob_matrix(y,prob_matrix,n,m):
    s_max = 0
    indeks = 0
    for i in range(n-m+1):
        s = 0
        for j in range(m):
            s+= np.log(prob_matrix[int(y[j]),j])
        if s > s_max:
            s_max = s
            indeks = i
    return s_max, y[indeks:indeks+m]

In [7]:
@njit
def update_matrix(sorted_indices, nizovi, matrix, granica=100):
    for i in sorted_indices[:granica]:
        for j, el in enumerate(nizovi[i]):
            matrix[int(el)][j] += 1
    return matrix


In [ ]:
@njit
def iteriraj_score(matrix, podaci, duljine, num_iter = 10):
    for i in range(num_iter):
        
        prob_matrix = matrix.copy()
        s  = np.sum(matrix, axis= 0)
        prob_matrix = prob_matrix/s
        
        scores = np.zeros((podaci.shape[0],))
        nizovi = np.zeros((podaci.shape[0],matrix.shape[1]))

        for j in range(podaci.shape[0]):
            print(i,j)
            n = int(duljine[j])
            m = matrix.shape[1]
            y = podaci[j,:m]

            score, niz = score_from_prob_matrix(y,prob_matrix,n,m)
            
            scores[j] = score
            nizovi[j,:] = niz

        sorted_indices = np.argsort(scores)[::-1]    
        
            
        matrix = update_matrix(sorted_indices, nizovi, matrix)

    return matrix, sorted_indices


In [19]:
matrix = np.ones((len(amino_acids),10))
matrix = update_matrix(sorted_indices, nizovi, matrix)

array([120., 120., 120., 120., 120., 120., 120., 120., 120., 120.])

In [125]:
print(type(matrix))
print(type(podaci))
print(type(duljine))

<class 'numpy.ndarray'>
<class 'numpy.ndarray'>
<class 'numpy.ndarray'>


In [22]:
matrix, sorted_indices = iteriraj_score(matrix, podaci, duljine)

0
0 0
0 1
0 2
0 3
0 4
0 5
0 6
0 7
0 8
0 9
0 10
0 11
0 12
0 13
0 14
0 15
0 16
0 17
0 18
0 19
0 20
0 21
0 22
0 23
0 24
0 25
0 26
0 27
0 28
0 29
0 30
0 31
0 32
0 33
0 34
0 35
0 36
0 37
0 38
0 39
0 40
0 41
0 42
0 43
0 44
0 45
0 46
0 47
0 48
0 49
0 50
0 51
0 52
0 53
0 54
0 55
0 56
0 57
0 58
0 59
0 60
0 61
0 62
0 63
0 64
0 65
0 66
0 67
0 68
0 69
0 70
0 71
0 72
0 73
0 74
0 75
0 76
0 77
0 78
0 79
0 80
0 81
0 82
0 83
0 84
0 85
0 86
0 87
0 88
0 89
0 90
0 91
0 92
0 93
0 94
0 95
0 96
0 97
0 98
0 99
0 100
0 101
0 102
0 103
0 104
0 105
0 106
0 107
0 108
0 109
0 110
0 111
0 112
0 113
0 114
0 115
0 116
0 117
0 118
0 119
0 120
0 121
0 122
0 123
0 124
0 125
0 126
0 127
0 128
0 129
0 130
0 131
0 132
0 133
0 134
0 135
0 136
0 137
0 138
0 139
0 140
0 141
0 142
0 143
0 144
0 145
0 146
0 147
0 148
0 149
0 150
0 151
0 152
0 153
0 154
0 155
0 156
0 157
0 158
0 159
0 160
0 161
0 162
0 163
0 164
0 165
0 166
0 167
0 168
0 169
0 170
0 171
0 172
0 173
0 174
0 175
0 176
0 177
0 178
0 179
0 180
0 181
0 182
0 183
0 18

In [9]:
truth = []

with open("zad4_ATBioPositives.txt", "r") as f:
    for line in f:
        line = line.strip()
        truth.append(line)


In [62]:
names = []

with open("zad4_AT_imena.txt", "r") as f:
    for line in f:
        line = line.strip()
        if line.startswith(">"):
            # Ukloni znak '>' i podijeli po '|'
            parts = line[1:].split('|')
            
            names.append(parts[0][:-3])

In [10]:
names = []

with open("zad4_AT_imena.txt", "r") as f: # tu ucitavam sva imena
    for line in f:
        line = line.strip()
        if line.startswith(">"):
            # Ukloni znak '>' i podijeli po '|'
            parts = line[1:].split('|')
            
            names.append(parts[0][:-3])


In [11]:
truth = []

with open("zad4_ATBioPositives.txt", "r") as f: #tu u truth stavljam one koji su pozitivni tj slicni testu
    for line in f:
        line = line.strip()
        truth.append(line)


In [17]:
tprs = []
fprs = []

positives  = list(set([names[i] for i in sorted_indices[:100]]))

tp = 0
fp = 0
tn = 0
fn = 0

print()
for name in positives:
    if name in truth:
        tp += 1
    else:
        fp +=1

ukupno = len(scores)
pozitivnih = len(truth)
negativnih = ukupno - pozitivnih # = fp + tn
tn = negativnih - fp
fn = pozitivnih - tp  

print(tp)

tpr = tp / (tp + fn) if (tp + fn) > 0 else 0
fpr = fp / (fp + tn) if (fp + tn) > 0 else 0
precision = tp / (tp+fp)


f1 = 2* (precision * tpr)/(precision + tpr)

print(tpr, fpr, len(positives))
print(f1)
tprs.append(tpr)
fprs.append(fpr)


0


ZeroDivisionError: float division by zero